In [1]:
import jsbsim
import numpy as np
import pandas as pd
from xml.dom import minidom
import time


1. change the data to lower number of points
2. play around with the initial state
3. shift between points based on distance to the target waypoint and the altitude, may be (speed)
4. if still lacking, design a better controller (look into the 737ap.xml) and make changes -
    a. airspeed control
    b. PID tuning

In [2]:
# render = True
# fdm = jsbsim.FGFDMExec("./jsbsim", None)
# fdm.load_model("737")

In [3]:
# if render:
#     fdm.set_output_directive("data_output/flightgear.xml")

In [4]:
trajectory = pd.read_excel("B747-200.xlsx", sheet_name=1)
trajectory

time_s  long_rad   lat_rad         alt_m       vt_ms       mass(kg)
0      600.943005  2.024995  0.693455   3896.154051  146.325266  252161.320662
1      602.277079  2.024960  0.693471   3902.297754  147.286012  252151.869851
2      603.590858  2.024926  0.693486   3908.382338  148.231306  252142.560025
3      604.885612  2.024892  0.693501   3914.411504  149.162017  252133.382330
4      606.161646  2.024858  0.693517   3920.384627  150.078323  252124.334761
...           ...       ...       ...           ...         ...            ...
7118  2102.565931  1.952187  0.697580  10001.227693  253.339818  245805.704114
7119  2102.706618  1.952182  0.697577  10001.227693  253.339818  245805.287107
7120  2102.847306  1.952176  0.697574  10001.227693  253.339818  245804.870100
7121  2102.987993  1.952170  0.697571  10001.227693  253.339818  245804.453094
7122  2103.128680  1.952164  0.697567  10001.227693  253.339818  245804.036088

[7123 rows x 6 columns]

In [5]:
waypoints = trajectory.loc[:, ["long_rad", "lat_rad", "alt_m", "vt_ms"]]
waypoints

long_rad   lat_rad         alt_m       vt_ms
0     2.024995  0.693455   3896.154051  146.325266
1     2.024960  0.693471   3902.297754  147.286012
2     2.024926  0.693486   3908.382338  148.231306
3     2.024892  0.693501   3914.411504  149.162017
4     2.024858  0.693517   3920.384627  150.078323
...        ...       ...           ...         ...
7118  1.952187  0.697580  10001.227693  253.339818
7119  1.952182  0.697577  10001.227693  253.339818
7120  1.952176  0.697574  10001.227693  253.339818
7121  1.952170  0.697571  10001.227693  253.339818
7122  1.952164  0.697567  10001.227693  253.339818

[7123 rows x 4 columns]

In [6]:
print(waypoints.values[0])

[2.02499451e+00 6.93454836e-01 3.89615405e+03 1.46325266e+02]


In [7]:
"""'ic/vc-kts (RW)',
'ic/ve-kts (RW)',
'ic/vg-kts (RW)',
'ic/vt-kts (RW)',
'ic/mach (RW)',
'ic/roc-fpm (RW)',
'ic/gamma-deg (RW)',
'ic/alpha-deg (RW)',
'ic/beta-deg (RW)',
'ic/theta-deg (RW)',
'ic/phi-deg (RW)',
'ic/psi-true-deg (RW)',
'ic/lat-gc-deg (RW)',
'ic/long-gc-deg (RW)',
'ic/h-sl-ft (RW)',
'ic/h-agl-ft (RW)',
'ic/terrain-elevation-ft (RW)',
'ic/vg-fps (RW)',
'ic/vt-fps (RW)',
'ic/vw-bx-fps (R)',
'ic/vw-by-fps (R)',
'ic/vw-bz-fps (R)',
'ic/vw-north-fps (R)',
'ic/vw-east-fps (R)',
'ic/vw-down-fps (R)',
'ic/vw-mag-fps (R)',
'ic/vw-dir-deg (RW)',
'ic/roc-fps (RW)',
'ic/u-fps (RW)',
'ic/v-fps (RW)',
'ic/w-fps (RW)',
'ic/vn-fps (RW)',
'ic/ve-fps (RW)',
'ic/vd-fps (RW)',
'ic/gamma-rad (RW)',
'ic/alpha-rad (RW)',
'ic/theta-rad (RW)',
'ic/beta-rad (RW)',
'ic/phi-rad (RW)',
'ic/psi-true-rad (RW)',
'ic/lat-gc-rad (RW)',
'ic/long-gc-rad (RW)',
'ic/p-rad_sec (RW)',
'ic/q-rad_sec (RW)',
'ic/r-rad_sec (RW)',
'ic/lat-geod-rad (RW)',
'ic/lat-geod-deg (RW)',
'ic/geod-alt-ft (R)',
'ic/targetNlf (RW)'
<set name="propulsion/engine[0]/set-running" value="1"/>
<set name="propulsion/engine[1]/set-running" value="1"/>
<set name="ap/altitude_setpoint" action="FG_EXP" value="1000.0" tc="10.0"/>"""

'\'ic/vc-kts (RW)\',\n\'ic/ve-kts (RW)\',\n\'ic/vg-kts (RW)\',\n\'ic/vt-kts (RW)\',\n\'ic/mach (RW)\',\n\'ic/roc-fpm (RW)\',\n\'ic/gamma-deg (RW)\',\n\'ic/alpha-deg (RW)\',\n\'ic/beta-deg (RW)\',\n\'ic/theta-deg (RW)\',\n\'ic/phi-deg (RW)\',\n\'ic/psi-true-deg (RW)\',\n\'ic/lat-gc-deg (RW)\',\n\'ic/long-gc-deg (RW)\',\n\'ic/h-sl-ft (RW)\',\n\'ic/h-agl-ft (RW)\',\n\'ic/terrain-elevation-ft (RW)\',\n\'ic/vg-fps (RW)\',\n\'ic/vt-fps (RW)\',\n\'ic/vw-bx-fps (R)\',\n\'ic/vw-by-fps (R)\',\n\'ic/vw-bz-fps (R)\',\n\'ic/vw-north-fps (R)\',\n\'ic/vw-east-fps (R)\',\n\'ic/vw-down-fps (R)\',\n\'ic/vw-mag-fps (R)\',\n\'ic/vw-dir-deg (RW)\',\n\'ic/roc-fps (RW)\',\n\'ic/u-fps (RW)\',\n\'ic/v-fps (RW)\',\n\'ic/w-fps (RW)\',\n\'ic/vn-fps (RW)\',\n\'ic/ve-fps (RW)\',\n\'ic/vd-fps (RW)\',\n\'ic/gamma-rad (RW)\',\n\'ic/alpha-rad (RW)\',\n\'ic/theta-rad (RW)\',\n\'ic/beta-rad (RW)\',\n\'ic/phi-rad (RW)\',\n\'ic/psi-true-rad (RW)\',\n\'ic/lat-gc-rad (RW)\',\n\'ic/long-gc-rad (RW)\',\n\'ic/p-rad_sec (RW)\',\

In [8]:

mToFeet = 3.2808399
def traj_init(wpt):
    global fdm
    fdm.set_property_value("ic/long-gc-rad", wpt[0][0])
    fdm.set_property_value("ic/lat-gc-rad", wpt[0][1])
    fdm.set_property_value("ic/h-sl-ft", mToFeet*wpt[0][2])
    fdm.set_property_value("ic/vt-fps", mToFeet*wpt[0][3])
    
    fdm.set_property_value("propulsion/engine[0]/set-running", 1)
    fdm.set_property_value("propulsion/engine[1]/set-running", 1)
    
    fdm.set_property_value("guidance/target_wp_longitude_rad", wpt[1][0])
    fdm.set_property_value("guidance/target_wp_latitude_rad", wpt[1][1])
    fdm.set_property_value('ap/altitude_setpoint', mToFeet*wpt[1][2])
    fdm.set_property_value('ap/airspeed_setpoint', mToFeet*wpt[1][3])
    
    fdm.set_property_value("ap/heading-setpoint", 0)
    fdm.set_property_value("ap/heading-setpoint-select", 0)
    fdm.set_property_value("ap/heading_hold", 1)
    fdm.set_property_value("ap/active-waypoint", 0)
    fdm.run()
    
    print(fdm["simulation/sim-time-sec"])
    

# initialization script

<?xml version="1.0" encoding="utf-8"?>
<initialize name="cruise">
  <!--
    This file sets up the aircraft to start off
    at cruise conditions.
  -->
  <altitude unit="FT"> 30000.0 </altitude>
  <vt unit="FT/SEC">     750.0 </vt>
  <gamma unit="DEG">       0.0 </gamma>
  <latitude unit="DEG">   47.0 </latitude>
  <longitude unit="DEG"> 122.0 </longitude>
  <phi unit="DEG">         0.0 </phi>
  <psi unit="DEG">       225.0 </psi>
  <beta unit="DEG">        0.0 </beta>
</initialize>

In [9]:
import math
def get_bearing(lat1, long1, lat2, long2):
    dLon = (long2 - long1)

    y = math.sin(dLon) * math.cos(lat2)
    x = math.cos(lat1) * math.sin(lat2) - math.sin(lat1) * math.cos(lat2) * math.cos(dLon)

    brng_rad = math.atan2(y, x)

    brng_deg = np.rad2deg(brng_rad)

    return brng_rad, brng_deg


lat1 = waypoints.values[0][1]
long1 = waypoints.values[0][0]
lat2 = waypoints.values[1][1]
long2 = waypoints.values[1][0]
get_bearing(lat1, long1, lat2, long2)

(-1.0371321086678496, -59.423292624171246)

In [11]:
init_state = {
    "longitude": waypoints.values[0][0],
    "latitude": waypoints.values[0][1],
    "altitude": mToFeet*waypoints.values[0][2],
    "vt": mToFeet*waypoints.values[0][3],
    "psi": get_bearing(lat1, long1, lat2, long2)[0],
    "theta": 20,
    "alpha": 10,
}

init = minidom.parseString("<initialize name=\"Trajectory Init\" />")
root = init.documentElement
# longitude
longitude = init.createElement("longitude")
longitude.setAttribute("unit", "RAD")
longitude.appendChild(init.createTextNode(str(init_state["longitude"])))
root.appendChild(longitude)
# latitude
latitude = init.createElement("latitude")
latitude.setAttribute("unit", "RAD")
latitude.appendChild(init.createTextNode(str(init_state["latitude"])))

root.appendChild(latitude)
# altitude
altitude = init.createElement("altitude")
altitude.setAttribute("unit", "FT")
altitude.appendChild(init.createTextNode(str(init_state["altitude"])))
root.appendChild(altitude)
# vt
vt = init.createElement("vt")
vt.setAttribute("unit", "FT/SEC")
vt.appendChild(init.createTextNode(str(init_state["vt"])))
root.appendChild(vt)
# psi  
psi = init.createElement("psi")
psi.setAttribute("unit", "RAD")
psi.appendChild(init.createTextNode(str(init_state["psi"])))
root.appendChild(psi)

# theta
theta = init.createElement("theta")
theta.setAttribute("unit", "DEG")
theta.appendChild(init.createTextNode(str(init_state["theta"])))
root.appendChild(theta)

# alpha
alpha = init.createElement("alpha")
alpha.setAttribute("unit", "DEG")
alpha.appendChild(init.createTextNode(str(init_state["alpha"])))
root.appendChild(alpha)

# # beta
# beta = init.createElement("beta")
# beta.setAttribute("unit", "RAD")
# beta.appendChild(init.createTextNode(str(init_state["beta"])))
# root.appendChild(beta)
# # phi
# phi = init.createElement("phi")
# phi.setAttribute("unit", "RAD")
# phi
# phi.setAttribute("value", str(init_state["phi"]))
# root.appendChild(phi)
# # gamma
# gamma = init.createElement("gamma")
# gamma.setAttribute("unit", "RAD")
# gamma.setAttribute("value", str(init_state["gamma"]))
# root.appendChild(gamma)


print(init.toprettyxml())



<?xml version="1.0" ?>
<initialize name="Trajectory Init">
	<longitude unit="RAD">2.024994513224</longitude>
	<latitude unit="RAD">0.693454835693</latitude>
	<altitude unit="FT">12782.657665623867</altitude>
	<vt unit="FT/SEC">480.0697721535906</vt>
	<psi unit="RAD">-1.0371321086678496</psi>
	<theta unit="DEG">20</theta>
	<alpha unit="DEG">10</alpha>
</initialize>



In [12]:
path_file = "./jsbsim/aircraft/737/737_traj_init.xml"
with open(path_file, "w") as f:
    f.write(init.toprettyxml())

In [13]:
# import jsbsim
# fdm = jsbsim.FGFDMExec("./jsbsim", None)
# fdm.load_model("737")
# fdm.load_ic("737_traj_init", True)
# fdm.run_ic()
# fdm.print_simulation_configuration()

In [23]:
## get 20 waypoints
len(waypoints.values)/20

356.15

In [14]:
# init the simulation
# traj_init(waypoints.values[0:2])

In [15]:

# fdm.run_ic()
# fdm.print_simulation_configuration()

# 2. Script for waypoint navigation

In [10]:
script = minidom.parseString("<runscript xmlns:xsi=\"http://www.w3.org/2001/XMLSchema-instance\" xsi:noNamespaceSchemaLocation=\"http://jsbsim.sf.net/JSBSimScript.xsd\" name=\"737 Flight\" />")

doc = script.documentElement
description = script.createElement("description")
description.appendChild(script.createTextNode("737 Flight test"))
doc.appendChild(description)

# aircraft used and initialization
use = script.createElement("use")
use.setAttribute("aircraft", "737")
use.setAttribute("initialize", "737_traj_init")
doc.appendChild(use)

# run the simulation
run = script.createElement("run")
run.setAttribute("start", "0.0")
run.setAttribute("end", "3600.0")
run.setAttribute("dt", "0.02")
doc.appendChild(run)

# initial event: engines are running and set 1st waypoint
init_event = script.createElement("event")
init_event.setAttribute("name", "set the engines running")
run.appendChild(init_event)
condition = script.createElement("condition")
condition.appendChild(script.createTextNode("simulation/sim-time-sec lt 0.1"))
init_event.appendChild(condition)

# "fcs/advance-cmd-norm[0]", "fcs/advance-cmd-norm[1]", "fcs/mixture-cmd-norm[0]", "fcs/mixture-cmd-norm[1]", "fcs/throttle-cmd-norm[0]", "fcs/throttle-cmd-norm[1]"

properties = ["fcs/advance-cmd-norm[0]", "fcs/advance-cmd-norm[1]", "fcs/mixture-cmd-norm[0]", "fcs/mixture-cmd-norm[1]", "fcs/throttle-cmd-norm[0]", "fcs/throttle-cmd-norm[1]", "propulsion/engine[0]/set-running", "propulsion/engine[1]/set-running",  "guidance/target_wp_longitude_rad", "guidance/target_wp_latitude_rad", "ap/altitude_setpoint", "ap/altitude_hold", "ap/airspeed_setpoint", "ap/heading_setpoint", "ap/heading-setpoint-select", "ap/heading_hold", "ap/active-waypoint", "ap/attitude_hold"]

values = [1,1,1,1,1,1, 1, 1, waypoints.values[1][0], waypoints.values[1][1], mToFeet*waypoints.values[1][2], 0, mToFeet*waypoints.values[1][3], -1.0371321086678496, 0, 1, 0, 0]
for prop, val in zip(properties, values):
    set = script.createElement("set")
    if prop in ["ap/altitude_setpoint", "ap/airspeed_setpoint"]:
        set.setAttribute("action", "FG_EXP")
        set.setAttribute("tc", "5")
    set.setAttribute("name", prop)
    set.setAttribute("value", str(val))
    init_event.appendChild(set) 

def notification(event):
    global script
    notify = script.createElement("notify")
    notify.setAttribute("format", "kml")
    event.appendChild(notify)
    notes = {"longitude": "position/long-gc-rad", "latitude": "position/lat-gc-rad", "altitude": "position/h-sl-meters", "airspeed": "velocities/vtrue-fps", "sim-time": "simulation/sim-time-sec"}
    for key, val in notes.items():
        property = script.createElement("property")
        property.setAttribute("caption", key)
        property.appendChild(script.createTextNode(val))
        notify.appendChild(property)

notification(init_event)

# event: head the 1st waypoint
event = script.createElement("event")
event.setAttribute("name", "head the 1st waypoint")
run.appendChild(event)
condition = script.createElement("condition")
event.appendChild(condition)
condition.appendChild(script.createTextNode("position/h-sl-meters gt 1000.0"))
condition.appendChild(script.createTextNode("ap/active-waypoint eq 0"))
set = script.createElement("set")
event.appendChild(set)
set.setAttribute("name", "ap/heading-setpoint-select")
set.setAttribute("value", "1")
set = script.createElement("set")
event.appendChild(set)
set.setAttribute("name", "ap/altitude_hold")
set.setAttribute("value", "1")
set = script.createElement("set")
event.appendChild(set)
set.setAttribute("name", "ap/active-waypoint")
set.setAttribute("value", "1")

notification(event)

# terminate the script
last_wpt = len(waypoints.values)-1
terminate = script.createElement("event")
terminate.setAttribute("name", "terminate the simulation")
run.appendChild(terminate)
condition = script.createElement("condition")
terminate.appendChild(condition)
condition.appendChild(script.createTextNode("guidance/wp-distance lt 100"))
condition.appendChild(script.createTextNode("ap/active-waypoint eq " + str(last_wpt)))
set = script.createElement("set")
terminate.appendChild(set)
set.setAttribute("name", "simulation/terminate")
set.setAttribute("value", "1")
notification(terminate)

# set the waypoints in reverse order

for i in range(len(waypoints.values)-1, 1, -1):
    event = script.createElement("event")
    event.setAttribute("name", "set the waypoint " + str(i))
    run.appendChild(event)
    condition = script.createElement("condition")
    event.appendChild(condition)
    condition.appendChild(script.createTextNode("ap/active-waypoint eq " + str(i-1)))
    condition.appendChild(script.createTextNode("guidance/wp-distance lt 1000"))
    set = script.createElement("set")
    event.appendChild(set)
    set.setAttribute("name", "guidance/target_wp_longitude_rad")
    set.setAttribute("value", str(waypoints.values[i][0]))
    set = script.createElement("set")
    event.appendChild(set)
    set.setAttribute("name", "guidance/target_wp_latitude_rad")
    set.setAttribute("value", str(waypoints.values[i][1]))
    set = script.createElement("set")
    event.appendChild(set)
    set.setAttribute("name", "ap/altitude_setpoint")
    set.setAttribute("value", str(mToFeet*waypoints.values[i][2]))
    set.setAttribute("action", "FG_EXP")
    set.setAttribute("tc", "2")
    # set = script.createElement("set")
    # event.appendChild(set)
    # set.setAttribute("name", "ap/altitude_hold")
    # set.setAttribute("value", "1")
    set = script.createElement("set")
    event.appendChild(set)
    set.setAttribute("name", "ap/airspeed_setpoint")
    set.setAttribute("value", str(mToFeet*waypoints.values[i][3]))
    set.setAttribute("action", "FG_EXP")
    set.setAttribute("tc", "2")
    set = script.createElement("set")
    event.appendChild(set)
    set.setAttribute("name", "ap/active-waypoint")
    set.setAttribute("value", str(i))
    
    notification(event)

# output some properties into an excel file
out = script.createElement("output")
doc.appendChild(out)
out.setAttribute("name", "737_simulation_data.csv")
out.setAttribute("type", "CSV")
out.setAttribute("rate", "10")
out.setAttribute("file", "unitconversions.xml")
props = ["simulation/sim-time-sec", "position/long-gc-rad", "position/lat-gc-rad", "position/h-sl-meters", "velocities/vtrue-fps"]
for prop in props:
    property = script.createElement("property")
    property.setAttribute("caption", prop)
    if prop in ["velocities/vtrue-fps"]:
        property.setAttribute("apply", "convert-fps-To-m_s")
    property.appendChild(script.createTextNode(prop))
    out.appendChild(property)

print(script.toprettyxml())

<?xml version="1.0" ?>
<runscript xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xsi:noNamespaceSchemaLocation="http://jsbsim.sf.net/JSBSimScript.xsd" name="737 Flight">
	<description>737 Flight test</description>
	<use aircraft="737" initialize="737_traj_init"/>
	<run start="0.0" end="3600.0" dt="0.02">
		<event name="set the engines running">
			<condition>simulation/sim-time-sec lt 0.1</condition>
			<set name="fcs/advance-cmd-norm[0]" value="1"/>
			<set name="fcs/advance-cmd-norm[1]" value="1"/>
			<set name="fcs/mixture-cmd-norm[0]" value="1"/>
			<set name="fcs/mixture-cmd-norm[1]" value="1"/>
			<set name="fcs/throttle-cmd-norm[0]" value="1"/>
			<set name="fcs/throttle-cmd-norm[1]" value="1"/>
			<set name="propulsion/engine[0]/set-running" value="1"/>
			<set name="propulsion/engine[1]/set-running" value="1"/>
			<set name="guidance/target_wp_longitude_rad" value="2.024960015079"/>
			<set name="guidance/target_wp_latitude_rad" value="0.693470510755"/>
			<set action="

In [11]:
# remaining_wpts = waypoints.values[2:]
# print(len(remaining_wpts), len(waypoints.values))
# print(waypoints.values[7122])
# for i in range(len(waypoints.values)-1, 1, -1):
#     print(i)

In [12]:
sim_script = "./jsbsim/scripts/737_traj_follow.xml"
with open(sim_script, "w") as f:
    f.write(script.toprettyxml())

In [20]:
# import jsbsim

### Simulation Properties
sleep_period = 0.01
realtime = True
nice = False
suspend = False
end = 1E99

fdm = jsbsim.FGFDMExec("./jsbsim", None)
fdm.set_output_directive("data_output/flightgear.xml")
fdm.load_script("scripts/737_traj_follow.xml")
fdm.run_ic()
fdm.print_simulation_configuration()

frame_duration = fdm.get_delta_t()
sleep_nseconds = (frame_duration if realtime else sleep_period) * 1E9
current_seconds = initial_seconds = time.time()
result = fdm.run()

while result and fdm.get_sim_time() <= end:
    fdm.check_incremental_hold()
    if fdm.holding():
        suspend = True
        paused_seconds = time.time() - current_seconds
        result = fdm.run()
    else:
        if realtime:
            if suspend:
                initial_seconds += paused_seconds
                suspend = False
            current_seconds = time.time()
            actual_elapsed_time = current_seconds - initial_seconds
            sim_lag_time = actual_elapsed_time - fdm.get_sim_time()

            for _ in range(int(sim_lag_time / frame_duration)):
                result = fdm.run()
                current_seconds = time.time()
                if fdm.holding():
                    break
        else:
            result = fdm.run()

    if nice:
        time.sleep(sleep_nseconds / 1000000.0)



In file ./jsbsim/aircraft/737/737.xml: line 913
      Property fcs/aileron-cmd-norm is already defined.

In file ./jsbsim/aircraft/737/737.xml: line 914
      Property fcs/elevator-cmd-norm is already defined.

In file ./jsbsim/aircraft/737/737.xml: line 915
      Property fcs/rudder-cmd-norm is already defined.

In file ./jsbsim/aircraft/737/737.xml: line 916
      Property fcs/throttle-cmd-norm[0] is already defined.

In file ./jsbsim/aircraft/737/737.xml: line 917
      Property fcs/throttle-cmd-norm[1] is already defined.

In file ./jsbsim/aircraft/737/737.xml: line 918
      Property simulation/terminate is already defined.


KeyboardInterrupt: 

JSBSim.py --root "./jsbsim" --script "scripts/737_traj_follow.xml" --logdirectivefile "data_output/flightgear.xml" --realtime

In [4]:
fdm.get_property_catalog()

['inertial/sea-level-radius_ft (R)',
 'simulation/gravity-model (RW)',
 'simulation/integrator/rate/rotational (RW)',
 'simulation/integrator/rate/translational (RW)',
 'simulation/integrator/position/rotational (RW)',
 'simulation/integrator/position/translational (RW)',
 'simulation/write-state-file (W)',
 'simulation/channel-dt (R)',
 'simulation/gravitational-torque (RW)',
 'simulation/force-output (W)',
 'simulation/do_simple_trim (W)',
 'simulation/reset (W)',
 'simulation/disperse (R)',
 'simulation/randomseed (RW)',
 'simulation/terminate (RW)',
 'simulation/pause (RW)',
 'simulation/sim-time-sec (R)',
 'simulation/dt (R)',
 'simulation/jsbsim-debug (RW)',
 'simulation/frame (RW)',
 'simulation/trim-completed (RW)',
 'simulation/output/log_rate_hz (RW)',
 'simulation/output/enabled (RW)',
 'velocities/h-dot-fps (R)',
 'velocities/v-north-fps (R)',
 'velocities/v-east-fps (R)',
 'velocities/v-down-fps (R)',
 'velocities/u-fps (R)',
 'velocities/v-fps (R)',
 'velocities/w-fps (R)

In [79]:
fdm['position/lat-gc-rad'], fdm['position/long-gc-rad'], fdm['position/h-sl-meters'], fdm['ic/vt-fps']

(0.6934548356929738, 2.024994513224, 3896.15405645645, 480.0697721535906)

In [80]:
"""<set name="ap/altitude_setpoint" action="FG_EXP" value="1000.0" tc="10.0"/>
<set name="ap/attitude_hold" value="0"/>
<set name="guidance/target_wp_latitude_rad" value="0.517238"/>
<set name="guidance/target_wp_longitude_rad" value="-1.662727"/>
<set name="ap/heading_setpoint" value="0"/>
<set name="ap/heading-setpoint-select" value="0"/>
<set name="ap/heading_hold" value="1"/>
<set name="ap/active-waypoint" value="0"/>"""

'<set name="ap/altitude_setpoint" action="FG_EXP" value="1000.0" tc="10.0"/>\n<set name="ap/attitude_hold" value="0"/>\n<set name="guidance/target_wp_latitude_rad" value="0.517238"/>\n<set name="guidance/target_wp_longitude_rad" value="-1.662727"/>\n<set name="ap/heading_setpoint" value="0"/>\n<set name="ap/heading-setpoint-select" value="0"/>\n<set name="ap/heading_hold" value="1"/>\n<set name="ap/active-waypoint" value="0"/>'

1. head to the first waypoint: 
"""
    <condition>position/h-agl-ft  ge  800</condition>
      <set name="ap/heading-setpoint-select" value="1"/>
      <set name="ap/active-waypoint" value="1"/>
"""
2. set the second waypoint:
"""
<condition>
  guidance/wp-distance lt 700
  ap/active-waypoint eq 1
</condition>
<set name="guidance/target_wp_latitude_rad" value="0.517533"/>
<set name="guidance/target_wp_longitude_rad" value="-1.663076"/>
<set name="ap/active-waypoint" value="2"/>
"""
3.
... and so fourth


How to make it realtime?? with python script??
look at -> "python/RudderKick.py" file

In [81]:
dt = fdm.get_delta_t()
run_period = 100 # seconds

In [96]:
traj_init(waypoints.values[0:2])
fdm.run_ic()
current_active_waypoint = 1
for i in range(int(run_period/dt)):
    # init the simulation
    
    fdm.set_property_value('ap/heading-set-select', 1)
    fdm.set_property_value('ap/active-waypoint', 1)

    fdm.run()
    if i % 10 == 0:
        print(fdm['simulation/sim-time-sec'], fdm['guidance/wp-distance'], fdm['ap/active-waypoint'])
    if fdm['guidance/wp-distance'] <= 100 and fdm['ap/active-waypoint'] == current_active_waypoint:
        print('Reached waypoint ', current_active_waypoint)
        current_active_waypoint += 1
        
        fdm.set_property_value('guidance/target_wp_longitude_rad', waypoints.values[current_active_waypoint][0])
        fdm.set_property_value('guidance/target_wp_latitude_rad', waypoints.values[current_active_waypoint][1])
        fdm.set_property_value('ap/altitude_setpoint', value=mToFeet*waypoints.values[current_active_waypoint][2])
        fdm.set_property_value('ap/airspeed_setpoint', value=mToFeet*waypoints.values[current_active_waypoint][3])
        
        fdm.set_property_value('ap/active-waypoint', current_active_waypoint)
    time.sleep(dt)
    fdm.run()
        
        

574.5499999996418
574.5583333329752 68770.62223482627 1.0
Creating input TCP socket on port 5137
Creating input UDP socket on port 5139
Creating UDP socket on port 5550
Successfully connected to socket for output ...

  Mass Properties Report (English units: lbf, in, slug-ft^2)
                                      Weight    CG-X    CG-Y    CG-Z         Ixx         Iyy         Izz         Ixy         Ixz         Iyz
    Base Vehicle                     83000.0   639.0     0.0   -40.0    562000.0   1473000.0   1894000.0        -0.0      8000.0        -0.0
0   Fuel                             9929.44     520     -80     -18           0           0           0
1   Fuel                             9929.44     520      80     -18           0           0           0
2   Fuel                             3858.88     480       0     -18           0           0           0
                                                                                                                            

Could not bind to TCP input socket, error = 98
Could not bind to UDP input socket, error = 98


575.0583333329747 69010.81891698697 1.0
575.2249999996412 69090.75809978404 1.0
575.3916666663077 69170.63741116291 1.0
575.5583333329743 69250.45919209183 1.0
575.7249999996408 69330.2259015814 1.0
575.8916666663073 69409.94005451059 1.0
576.0583333329738 69489.60417246837 1.0
576.2249999996403 69569.22074776061 1.0
576.3916666663068 69648.79222053238 1.0
576.5583333329733 69728.32096822276 1.0
576.7249999996399 69807.80930592197 1.0
576.8916666663064 69887.25949547254 1.0
577.0583333329729 69966.67376065119 1.0
577.2249999996394 70046.0543057333 1.0
577.3916666663059 70125.40333482841 1.0
577.5583333329724 70204.72306980104 1.0
577.724999999639 70284.01576512233 1.0
577.8916666663055 70363.28371859337 1.0
578.058333332972 70442.52927746599 1.0
578.2249999996385 70521.75484000938 1.0
578.391666666305 70600.96285296364 1.0
578.5583333329715 70680.15580564995 1.0
578.724999999638 70759.33622150918 1.0
578.8916666663046 70838.50664812543 1.0
579.0583333329711 70917.66964660828 1.0
579.22

KeyboardInterrupt: 

In [91]:
fdm['position/lat-gc-rad'], fdm['position/long-gc-rad'], fdm['position/h-sl-meters']

(0.6934550270186491, 2.024994513224097, 3896.154057295561)

To log the results:
set the output directive file to a predefined xml file like "position"
and the simulation again NB: not in realtime


In [5]:
dt = fdm.get_delta_t()
print(dt, fdm['simulation/dt'])

0.008333333333333333 0.008333333333333333


In [8]:
fdm['position/lat-gc-deg'], fdm['position/long-gc-deg'], fdm['position/h-sl-meters']

(46.99999999999999, 122.0, 9144.05121923351)

In [16]:
realtime = False
end = 1E99
physics_per_second = int(1/dt)
pause_delay = 0.01

In [22]:
import time
def send_info(**kwargs):
    fdm['position/lat-gc-deg'] = kwargs.get('position/lat-gc-deg', 0)
    fdm['position/long-gc-deg'] = kwargs.get('position/long-gc-deg', 0)
    fdm['position/h-sl-meters'] = kwargs.get('position/h-sl-meters', 0)
    fdm['ic/psi-true-deg'] = kwargs.get('ic/psi-true-deg', 0)
    
    print(fdm['simulation/sim-time-sec'], fdm['position/lat-gc-deg'], fdm['position/long-gc-deg'], fdm['position/h-sl-meters'], fdm['ic/psi-true-deg'])
    
def step(**kwargs):
    #send_info(**kwargs)
    for i in range(int(pause_delay*physics_per_second)):
        if realtime:
            send_info(**kwargs)
            fdm.run()
            time.sleep(dt)
        else:
            send_info(**kwargs)
            fdm.run()
    

In [23]:
'position/lat-gc-deg (RW)',
'position/long-gc-deg (RW)',
'position/h-sl-meters (RW)'
'ic/psi-true-deg (RW)'
cmds = [{'position/lat-gc-deg': 47, 'position/long-gc-deg': 122.5, 'position/h-sl-meters': 10000, 'ic/psi-true-deg': 20,}, {'position/lat-gc-deg': 46.5, 'position/long-gc-deg': 122.5, 'position/h-sl-meters': 9500, 'ic/psi-true-deg': 22,}, {'position/lat-gc-deg': 46, 'position/long-gc-deg': 122.6, 'position/h-sl-meters': 9000, 'ic/psi-true-deg': 25,}]


In [24]:
send_info(**cmds[0])

0.049999999999999996 46.99999999999999 122.50000000000001 9999.999999999547 19.999999999999996


In [25]:
for i in range(len(cmds)):
    step(**cmds[i])

0.049999999999999996 47.0 122.50000000000001 9999.999999999547 19.999999999999996
0.05833333333333333 46.5 122.50000000000001 9500.000000000024 22.0
0.06666666666666667 45.99999999999999 122.60000000000001 9000.000000000502 25.0


In [ ]:
sleep_period = 0.01
frame_duration = dt
sleep_nseconds = (frame_duration if realtime else sleep_period) * 1E9
